In [6]:
import matplotlib.pyplot as plt
from graphics import *
from operator import *
from random import *
import numpy as np
import timeit
from math import *

a = 3
s = 3
r = 3
rr = 20
ro = 70
ra = 300
noise = 0.01
prop = 0.4
weight = 3
bias = np.array([0.0,-1.0])
dev_bias = 3
dTheta = 120
sight_theta = 180


In [7]:
def initialize_agents(speed, N, width, height):
    """
    Initializes our agent set with randomly directed speeds, draws the window and the agents
    """
    agents = [Point(width*random(), height*random()) for i in range(N)]
    speeds = [np.array([0.0, 0.0]) for i in range(N)]
    
    for i in range(N):
        theta = np.pi * random()
        speeds[i][0] = speed * np.cos(theta)
        speeds[i][1] = speed * np.sin(theta)

    return agents, speeds


def initialize_window(agents, width, height):
    win = GraphWin("Swarm", width, height) # size of box
    for agent in agents:
        agent.draw(win)
    win.getMouse()
    return win


def couple_speeds(agents, speeds, a, s, N):
    """
    Simplest model: for each agent, it will give its nearest neighbour a fraction of its speed and re-normalize it
    
    """
    nearest_neighbours = [nearest_neighbour(agent, agents, N) for agent in agents]
    for i in range(N):
        weightedSpeed = a * speeds[nearest_neighbours[i]]
        speeds[i] = speeds[i] + weightedSpeed
        speeds[i] = s * normalized(speeds[i])


def angle(vec1, vec2):  # (Not so) stupid way of doing an angle
    return np.arccos(np.dot(normalized(vec1),normalized(vec2)))
            
def get_distances(agent, agents, N):
    """
    Given one angent and the set of all agents, 
    computes the distances from the first to all of the others
    """
    dists = N * [0.0]
    for i in range(N):
        a, dists[i] = relative_pos(agent, agents[i])
        if dists[i] == 0:
            dists[i] = 0.1
    
    return dists

def relative_pos(agent1, agent2):
    dx = agent2.getX() - agent1.getX()
    dy = agent2.getY() - agent1.getY()

    return np.array([dx, dy]), np.linalg.norm([dx, dy])

def nearest_neighbour(agent, agents, N):
    """
    Returns the index for the agent with smallest Eucledian distance to agent in question
    """
    distances = get_distances(agent, agents, N)
    j = next(i for i in range(N) if agents[i] is agent)
    distances[j] = distances[j-1] + 1

    return distances.index(min(distances))


def softened_angle(speed, newspeed, s, maxTheta):
    theta = angle(speed, newspeed)
    if maxTheta**2 > theta**2:
        return s*newspeed
    else:
        return np.dot(rot_matrix(maxTheta), speed)    

def in_sight_range(rel_pos, speed1, angle_range):
    return 360*angle(speed1, rel_pos)/np.pi < angle_range
    

def noisy_vector(noise):
    return noise * np.array([2 * random() - 1, 2 * random() - 1])
    
def biaser(speeds, N, s, i, prop, bias, dev_bias, weight):
    #bias = np.array([0.0,1.0])
    #Ns has to be integer 
    Ns = int(N * prop)
    gbias = np.random.normal(bias, dev_bias, )
    for i in range(Ns):
        tot_dir = normalized(normalized(speeds[i]) + weight * gbias)
        
        if np.linalg.norm(tot_dir) != 0:
            speeds[i] = s*tot_dir
    #bias = np.dot(tot_dir,np.array([[np.cos(rot_bias*i), 0],[0, np.sin(rot_bias*i)]]))
    #return bias

def quality (agents, speeds, N, bias, window, old_cm):
#ACCURACY (DIRECTIONS DISTRIBUTION)
    dev = 0.0
    for i in range(N):
        dev += angle(bias, speeds[i])
    dev_avg = dev/(N*2*(np.pi))
    #print (dev_avg)
    
#ELONGATION: SHAPE OF SWARM
    #can be smarter if we make agents become poses before, more globally in  the code
    poses = [np.array([a.getX(), a.getY()]) for a in agents]
    #Center of Mass
    cm = np.mean(poses,axis=0)
    #Standard Deviation
    std = np.std(poses,axis=0)
    #print (cm, std)

    #Elongation >1 means 
    elong = std[1] / std[0]
    #Drawing it
    #old_cm = Point(cm[0],cm[1])
    #old_cm.draw(window)
    #old_cm.setFill("red")

#GROUP DIRECTION
    #Vector
    group_dir = np.array([cm[0] - old_cm[0], cm[1] - old_cm[1]])                
    #print (group_dir)
    # Norm
    group_dir = np.linalg.norm(group_dir)
    #print (group_dir)
    return cm
    


def rigid_boundary(x_bound, y_bound, agents, speeds, N):
    for i in range(N):
        [dx, dy] = [0, 0]
        [x, y] = [agents[i].getX(), agents[i].getY()]
        if x > x_bound:
            speeds[i][0] = -speeds[i][0]
            dx = x_bound - x         
        
        elif x < 0:
            speeds[i][0] = -speeds[i][0]
            dx = -x
        
        if y > y_bound:
            speeds[i][1] = -speeds[i][1]
            dy = y_bound - y
        
        elif y < 0:
            speeds[i][1] = -speeds[i][1]
            dy = -y

        agents[i].move(dx, dy)
        
        
def periodic_boundary(x_bound, y_bound, agents, speeds, N):  #Changed from rigid boundaries do periodic boundary condition
    [dx, dy] = [0, 0]
    for i in range(N):
        [x, y] = [agents[i].getX(), agents[i].getY()]
        if x > x_bound:
            dx = -x_bound         
        
        elif x < 0:
            dx = x_bound
        
        if y > y_bound:
            dy = -y_bound
        
        elif y < 0:
            dy = y_bound

        agents[i].move(dx, dy)

def next_step(agents, speeds, dt, N):
    dxvec = [dt * speeds[i][0] for i in range(N)]
    dyvec = [dt * speeds[i][1] for i in range(N)]
    for i in range(N):
        agents[i].move(dxvec[i], dyvec[i])
        

def normalized(vector):
    if vector[0] == vector[1] == 0:
        return vector
    return vector / np.linalg.norm(vector)


def rot_matrix(theta, unit = "None"):
    if unit in ["None", "deg"]:
        c, s = np.cos(pi * theta / 180), np.sin(pi * theta / 180)
    elif unit == "rad":
        c, s = np.cos(theta), np.sin(theta)
    return np.array([[c, -s],[s, c]])

def warn_me_args(N_steps, a, dt, N, width, height, s, rr, ro, ra, noise, prop, weight, bias, dTheta):
    if dt*s < rr:
        print("Warning - step length bigger the repultion radius.")
        

        
def virtualizer (current, agents, h, w, N):
    lower_limit = current.getY() - h / 2
    upper_limit = current.getY() + h / 2
    left_limit = current.getX() - w / 2
    right_limit = current.getX() + w / 2
    
    vagents=[np.array([agent.getX(),agent.getY()]) for agent in agents]
    virtuals = N * [0.0, 0.0]
    vvirtuals = N * [Point(0.0, 0.0)]

    for j in range(N):
        #make more compact!!!
        virtuals[j]=vagents[j]
        
        #newcopy = agents[i].clone()
        candidates = [vagents[j],
                      vagents[j]+[w,0],vagents[j]+[-w,0],vagents[j]+[w,h],vagents[j]+[w,-h],
                      vagents[j]+[-w,h],vagents[j]+[-w,-h],vagents[j]+[0,h],vagents[j]+[0,-h]]
        #print candidates
        
        #virtuals[j] = next((cand for cand in candidates if lower_limit < cand[1] < upper_limit and left_limit < cand[0] < right_limit),False
        for i in range(9):
            if lower_limit < candidates[i][1] < upper_limit and left_limit < candidates[i][0] < right_limit:
                virtuals[j]=candidates[i]
            
        ##ATTENTION HERE!!
#        if not virtuals[j]:
 #           virtuals[j] = agents[j]
        vvirtuals[j] = Point(virtuals[j][0],virtuals[j][1])
        
    return vvirtuals

        
#def get_v_avg(speeds, N):
#    return
#   
#def get_potencials(distances, N):
#    potentials = np.zeros(N, N)
#    for i in range(N):
#        for j in range(i+1,N):
#            potentials[i][j] = potentials[j][i] = morse_pot(distances[i][j])
#    return potentials  
#    
#def morse_pot(r, ca = 0.5, cr = 1, la = 3, lr = 0.5):
#    return cr*np.exp(-r/lr) - ca * np.exp(-r)
#
#def weird_paper(agents, N, dt):
#    distances = [get_distances(agent, agents) for agent in agents]
#    potencials = get_potencials(distances, N)
#    for i in range(N):
#            newSpeed = speed[i] + dt * potentials
#            speeds[i] = speeds[i] + weightedSpeed
#            speeds[i] = s * normalized(speeds[i]) ### PROBLEMA?-------------------------------------------------
#
#    return


In [ ]:
#COUZIN MODEL IMPLEMENTED WITH REPULSE, ATRACT AND ORIENT ZONES SEPARATED (1ST PAPER)
def couzin(agents, speeds, N, width, height, s, noise, dTheta, rr, ro, ra, sight_range, model2, roa, atract, orient):
    
    if not model2:
        atract = orient = 1
    # watch only particles in repulsion zone
    for i in range(N):
        r_dir = np.array([0.0, 0.0])
        o_dir = np.array([0.0, 0.0])
        a_dir = np.array([0.0, 0.0])
        repulsion_flag = False    
        
        virtuals = virtualizer(agents[i], agents, height, width, N)
        
        for j in range(N):     
            if i == j:
                #Eliminate the i-i interaction
                continue

            rel_pos, distance = relative_pos(agents[i], virtuals[j])
            
            if in_sight_range(rel_pos, speeds[i], sight_range):
                if distance < rr:
                    rel_pos = normalized(rel_pos)
                    r_dir = r_dir + rel_pos
                    repulsion_flag = True

                elif not repulsion_flag:
                    
                    if model2: # Couzin 2
                        if distance < roa:
                            o_dir = o_dir + speeds[j]
                            rel_pos = normalized(rel_pos)
                            a_dir = a_dir + rel_pos

                    else: # Couzin 1
                        if distance < ro:
                            o_dir = o_dir + speeds[j]

                        elif distance < ra:
                            rel_pos = normalized(rel_pos)
                            a_dir = a_dir + rel_pos

        #Out of for (j), we treat now the resulting direction vector
        if repulsion_flag:
            tot_dir =  normalized(- r_dir)
        else:
            tot_dir = orient * normalized(o_dir) + atract * normalized(a_dir)
            tot_dir = normalized(tot_dir)
            
        tot_dir = normalized(normalized(tot_dir) + noisy_vector(noise))
        
        #avoid pts stoping when not interacting
        if np.linalg.norm(tot_dir) != 0:
            speeds[i] = softened_angle(speeds[i], tot_dir, s, dTheta)
    return

    
def vicsek(agents, speeds, N, s, noise, r): # s=speed, noise= letter csi temperature factor, r=radius of interaction
    # consider only particles within 'r' from pt_i, align pt_i with v_avg
    for i in range(N):
        distances = get_distances(agents[i], agents)
        tot_dir = np.array([0.0, 0.0])
        
        for j in range(N):
            if distances[j] < r:
                tot_dir = tot_dir + speeds[j]

        tot_dir = s * normalized(normalized(tot_dir) + noise * np.array([(-1)+2*random(),(-1)+2*random()]))
        if np.linalg.norm(tot_dir) != 0:
            speeds[i] = tot_dir
    return

##MILL MODEL
def mill (dt, agents, speeds, N, width, height, cr, ca, lr, la, alpha, beta):
    clr = cr / lr
    cla = ca / la
    for i in range(N):
        u_dir = np.array([0.0, 0.0])
        propulsion = np.array([0.0, 0.0])
        friction = np.array([0.0, 0.0])
        grad_U = np.array([0.0, 0.0])
        
        virtuals = virtualizer(agents[i], agents, height, width, N)
        
        for j in range(N):   #Duality interactions, by the Morse potential  
            if i == j:
                #Eliminate the i-i interaction
                continue

            rel_pos, distance = relative_pos(agents[i], virtuals[j])
            u_dir = normalized(rel_pos)
            grad_U = grad_U + u_dir * (-clr*np.exp(-distance / lr) + cla *np.exp(- distance / la))
            
        propulsion = alpha * speeds[i] # self-propulsion propto alpha
        friction =  beta * ((normalized(speeds[i]))**2) * speeds[i] #friction force propto beta
        d_speed = propulsion - friction - grad_U
        speeds[i]= speeds[i]+dt*d_speed
        # speeds[i] 
        print propulsion, friction, grad_U
    return

def run(N_steps, N, s, dt, width, height):#N_steps, a, dt, N, width, height, s, rr, ro, ra, noise, prop, weight, bias, dev_bias, dTheta, sight_theta):
    """
    Simulates motion of swarm. Recieves following parameters:

    N_steps  - number of steps to perform
    a -  coupling between neighbouring points
    dt - time step to be used 
    N - number of points to be used
    width & heigth of window
    s - module of speed throughout agents

    """
    
    agents, speeds = initialize_agents(s, N, width, height)
    window = initialize_window(agents, width, height)
    old_cm=np.array([0.0,0.0])
    bias = np.array([0.0,-1.0])
    for i in range(N_steps):
        
        next_step(agents, speeds, dt, N)
        start = timeit.default_timer()
        ## MODEL
        #couple_speeds(agents, speeds, a, s, N)
        #vicsek(agents, speeds, N, s, 0.1, r = 500)
        #couzin(agents, speeds, N, width, height, s, noise, dTheta, rr, ro, ra, sight_theta, 1, 200, 1.5, 1) #(...)last 4 parameters: model2, roa, orient, atract
        #mill (dt, agents, speeds, N, width, height, cr=1.0, ca=0.5, lr=0.5, la=3.0, alpha=1.6, beta=0.5)
        mill (dt, agents, speeds, N, width, height, cr=100, ca=50, lr=50 la=300.0, alpha=1.6, beta=3.0)
        
        
        #interaction(agents, speeds)
        
        
        #biaser(speeds, N, s, i, prop, bias, dev_bias, weight)
        
        #INFORMATION TRANSFER: SHAPE & DIRECTION & ALIGNMENT QUALITY 
        #point_cm.undraw()
        #old_cm = quality(agents, speeds, N, bias, window, old_cm)
        
        ## BOUNDARY CONDITIONS
        rigid_boundary(width, height, agents, speeds, N)
        #periodic_boundary(width, height, agents, speeds, N)

        #time.sleep(0.02)
        stop = timeit.default_timer()
        #print stop - start
    window.close()
    return


In [ ]:
run(10000, 10, 5, 0.01, 500, 500)
# Field of view is around 340º for pigeons as saind in the source:
# https://www.quora.com/What-does-a-pigeons-field-of-view-look-like

[ 6.01034843  5.27974542] [ 6.3609246   4.31181625] [ -4.92871091e-11   2.10216970e-11]
[-7.95272138  0.86845994] [-14.73562633   0.01918981] [  4.02381572e-07   5.90631099e-07]
[ 4.78784577  6.40909766] [ 3.21544996  7.71279816] [ -4.03950999e-07  -5.83238199e-07]
[-6.60005208  4.52098579] [-8.42293377  2.70720239] [-0.00205765 -0.00062363]
[-7.64575821  2.35422627] [-13.09432084   0.3822662 ] [ -2.15356302e-11  -3.31066027e-11]
[-3.14715546  7.35495836] [ -0.913221   11.6563332] [  1.56942663e-09  -7.39289954e-09]
[-2.02751079  7.73881128] [ -0.24418041  13.5782583 ] [ 0.00205765  0.00062363]
[ 7.960451    0.79449344] [  1.47786349e+01   1.46923831e-02] [ -2.59938045e-10   2.68549301e-10]
[-0.95638793  7.9426269 ] [ -0.02562852  14.67958526] [  6.98259908e-11   8.76025458e-12]
[ 6.46956679  4.70581614] [ 7.93317254  3.0529955 ] [  1.52039848e-12   3.69792834e-12]
[ 6.00473921  5.29523229] [ 6.33359422  4.34333004] [ -4.84137178e-11   2.06319882e-11]
[-7.84419491  0.88204825] [-14.524

[-2.3209826   6.88685202] [ -0.44386812  11.59579583] [ 0.00222036  0.00066122]
[ 6.94097652  0.92760607] [ 12.78597113   0.03051847] [ -2.16174780e-10   2.20890881e-10]
[-1.11473352  6.93753229] [ -0.05260583  12.68048123] [  7.79843312e-11   9.92493935e-12]
[ 6.2726066   4.95074764] [ 7.24681447  3.5629962 ] [  1.51232392e-12   3.73173370e-12]
[ 5.96610579  5.43698265] [ 6.11117962  4.62515233] [ -4.06973712e-11   1.72319562e-11]
[-6.84669655  1.02879456] [-12.55410317   0.04259204] [  3.35855599e-07   4.82556178e-07]
[ 5.04165941  6.22081385] [ 3.74756845  7.03996794] [ -3.37419373e-07  -4.75476843e-07]
[-6.33244194  4.81543674] [-7.52301315  3.30815018] [-0.00223565 -0.00066503]
[-6.78889642  2.70620318] [-10.9838525    0.69572618] [ -3.90101285e-11  -3.05907579e-11]
[-3.5307403   6.69498651] [-1.44054746  9.82153494] [  1.56377394e-09  -7.07933514e-09]
[-2.35105195  6.81149834] [ -0.46926719  11.41199238] [ 0.00223565  0.00066503]
[ 6.84745661  0.94195947] [ 12.60053255   0.032801

[-6.19244347  3.02364801] [-9.37553799  1.09144974] [ -5.27401750e-11  -2.89882355e-11]
[-3.85003733  6.26000054] [-1.98115634  8.51622323] [  1.56524213e-09  -6.82505732e-09]
[-2.65322127  6.15076989] [-0.78045987  9.72341018] [ 0.00237875  0.00070378]
[ 5.99095538  1.09613427] [ 10.86918308   0.06657327] [ -1.78621850e-10   1.80574100e-10]
[-1.31300233  6.00795253] [ -0.11222312  10.75140759] [  8.62993180e-11   1.10572884e-11]
[ 6.13417905  5.17449594] [ 6.71986793  4.03362522] [  1.53230287e-12   3.83881826e-12]
[ 5.95300767  5.5700005 ] [ 5.95153938  4.87512426] [ -3.38971216e-11   1.43154421e-11]
[-5.92133471  1.21336063] [-10.65510038   0.09167869] [  2.82979847e-07   3.98836184e-07]
[ 5.25038151  6.10582912] [ 4.18484696  6.58174318] [ -2.84545462e-07  -3.92035420e-07]
[-6.16087972  5.05868498] [-6.89979579  3.81962698] [-0.0023921  -0.00070772]
[-6.14151396  3.05456318] [-9.23169312  1.13580132] [ -5.40149141e-11  -2.88553881e-11]
[-3.87993943  6.22390098] [-2.0359519   8.4038

[-5.70953803  3.34971495] [-7.9641166   1.60826738] [ -6.58893402e-11  -2.77441245e-11]
[-4.15651082  5.92499614] [-2.57042303  7.44529778] [  1.57061805e-09  -6.56566786e-09]
[-2.97488162  5.60290043] [-1.22666596  8.19513217] [ 0.00251631  0.00074782]
[ 5.20433479  1.2872036 ] [ 9.19559979  0.13913171] [ -1.49186846e-10   1.49380008e-10]
[-1.53357358  5.24812023] [-0.22621541  9.06608216] [  9.38545652e-11   1.20426782e-11]
[ 6.05446196  5.35889951] [ 6.36532812  4.41388455] [  1.57896798e-12   4.01463021e-12]
[ 5.96218836  5.68502175] [ 5.85542817  5.07619122] [ -2.83695256e-11   1.20207452e-11]
[-5.16107093  1.4202376 ] [-8.99579648  0.18745764] [  2.40381823e-07   3.32908782e-07]
[ 5.42294151  6.0427151 ] [ 4.5359791   6.27570671] [ -2.41953021e-07  -3.26366003e-07]
[-6.05758144  5.25871966] [-6.47680965  4.23743847] [-0.00252784 -0.00075189]
[-5.67346477  3.37757811] [-7.85411691  1.65717539] [ -6.69949081e-11  -2.76521543e-11]
[-4.18188823  5.90067131] [-2.62159803  7.36466695] 

[ 5.98460036  5.77806621] [ 5.80752764  5.22676971] [ -2.41644706e-11   1.03376189e-11]
[-4.60301964  1.62208993] [-7.6772708   0.33597206] [  2.08519090e-07   2.84543001e-07]
[ 5.55546001  6.01755126] [ 4.79299262  6.09124515] [ -2.10096133e-07  -2.78225191e-07]
[-6.00598921  5.41055315] [-6.2163572   4.54472198] [-0.00263488 -0.00079321]
[-5.37319587  3.63682943] [-6.9093991  2.1424518] [ -7.73159590e-11  -2.68880245e-11]
[-4.41345049  5.70285772] [-3.09972565  6.68753531] [  1.57704253e-09  -6.31780996e-09]
[-3.26713576  5.21247822] [-1.72784418  7.01674654] [ 0.00263488  0.00079321]
[ 4.56865465  1.49621979] [ 7.73645998  0.2717462 ] [ -1.25740749e-10   1.24809293e-10]
[-1.76814222  4.64569682] [-0.41946985  7.6085475 ] [  1.00643553e-10   1.28906417e-11]
[ 6.01631194  5.51262691] [ 6.13218831  4.71737334] [  1.64989832e-12   4.25707361e-12]
[ 5.98743352  5.78688695] [ 5.8043782   5.24045004] [ -2.37794907e-11   1.01868878e-11]
[-4.55383163  1.64266781] [-7.5553312   0.35462704] [ 

...

[-1473.89126269  1473.89151183] [-1381.77282521  1381.7735259 ] [  4.11400247e-14  -8.22797841e-14]
[-1143.09561007 -1143.09564784] [-1071.65209904 -1071.65220526] [ -4.07490627e-09  -8.86092388e-09]
[-1296.69953405  1296.69958012] [-1215.65576998  1215.65589956] [ -6.25451116e-06  -3.37397695e-06]
[ 1067.01266673 -1067.01247734] [ 1000.32455261 -1000.32401996] [  6.27072515e-09   8.26408014e-09]
[ 674.86894633 -674.86894582] [ 632.68963765 -632.68963624] [  6.25231524e-06   3.37457384e-06]
[ 739.99053212  739.99053433] [ 693.74112179  693.74112801] [ -8.97018671e-13  -1.23794623e-11]
[ 1489.09736285 -1489.0971484 ] [ 1396.02897871 -1396.02837558] [ -3.66203275e-15   8.41788620e-15]
[-1522.10287679 -1522.10350934] [-1426.97085398 -1426.97263302] [  6.88557677e-21   4.50209820e-21]
[ 705.97324709 -705.9733149 ] [ 661.84985557 -661.85004629] [  7.60420224e-13  -1.38552741e-13]
[-1496.53628718 -1496.53620942] [-1403.00284213 -1403.00262343] [  4.70537768e-14   2.41634929e-13]
[-1475.36515

[-1309.7250427   1309.72507734] [-1227.86719505  1227.86729249] [ -8.73076591e-11  -7.39698908e-11]
[ 1077.73091186 -1077.73077084] [ 1010.37286208 -1010.37246545] [ 0.00443003 -0.00242248]
[ 681.64808615 -681.64808524] [ 639.04508162 -639.04507906] [ -1.71338135e-05  -6.28164194e-06]
[ 747.42382626  747.42382791] [ 700.70983557  700.70984021] [  5.01130884e-20   1.60195534e-19]
[-1504.05549645 -1504.05533667] [-1410.05217771 -1410.05172834] [  1.04085822e-17   3.58708884e-18]
[-1537.39266697 -1537.39313826] [-1441.30518345 -1441.30650895] [  2.02673042e-13  -1.23621678e-13]
[ 713.06484213 -713.06489249] [ 668.49824229 -668.49838392] [ -3.73239703e-07  -1.15438364e-06]
[-1511.56916378 -1511.56910584] [-1417.09614536 -1417.09598241] [ -1.37210258e-13  -7.61396934e-13]
[-1490.18533957  1490.1855508 ] [-1397.04855781  1397.04915191] [ 0.0032717  -0.00665496]
[-1155.7327264  -1155.73275402] [-1083.49940511 -1083.49948279] [  3.73303634e-07   1.15446644e-06]
[-1311.03476826  1311.0348019 ] 

[ 1554.38886485  1554.38920581] [ 1457.23924115  1457.24020009] [ -2.70734283e-11   6.92757959e-11]
[ 720.94784179 -720.94798902] [ 675.88846365 -675.88887773] [ -6.07421652e-07  -4.50208103e-06]
[-1528.2798022  -1528.27976089] [-1432.76235329 -1432.76223711] [  6.07235684e-07   4.50233985e-06]
[-1506.65961856  1506.65992267] [-1412.49310729  1412.49396261] [  1.84552553e-10  -2.55915628e-10]
[-1168.50954675 -1168.50956674] [-1095.47768133 -1095.47773756] [ -2.79318671e-10  -3.93924069e-10]
[-1325.52847922 -1325.52850355] [-1242.68292645 -1242.68299489] [  1.41460789e-12  -2.90354216e-12]
[ 1090.73502102 -1090.7349877 ] [ 1022.56411345 -1022.56401972] [  2.39274901e-06   5.96399744e-06]
[ 689.87300348 -689.87300046] [ 646.7559436 -646.7559351] [ -2.36539608e-06  -5.97814515e-06]
[ 756.44240721  756.44240837] [ 709.16475567  709.16475893] [  3.06384166e-10   3.24647425e-10]
[-1522.20373698 -1522.20362474] [-1427.06610864 -1427.06579297] [ -2.73529231e-08   1.41477039e-08]
[ 1555.9432588

[ 728.91806055 -728.91816699] [ 683.36058197 -683.36088134] [ -2.64700544e-14  -1.58033408e-14]
[-1545.17519008 -1545.17514337] [-1448.60178448 -1448.60165313] [-0.00034106 -0.00014563]
[-1523.31603317  1523.31625348] [-1428.10857455  1428.10919418] [ -2.12757302e-14  -7.62827235e-14]
[ 1181.42738656 -1181.42749473] [ 1107.58807349 -1107.58837772] [ 0.00034106  0.00014563]
[-1340.1824195  -1340.18243685] [-1256.42100202 -1256.42105081] [  2.12741265e-14   7.62759158e-14]
[ 1102.79327207 -1102.79324791] [ 1033.86871522 -1033.86864727] [ -1.80268418e-09   8.81020893e-09]
[ 697.49966319 -697.49966074] [ 653.90593654 -653.90592965] [  1.80445886e-09  -8.80920543e-09]
[-764.80522267  764.8049029 ] [-717.00519603  717.00429668] [ -1.58598716e-12  -1.16142395e-12]
[-1539.03193479 -1539.03185402] [-1442.84251459 -1442.84228743] [  1.03965143e-16   4.70958308e-17]
[ 1573.14452416  1573.14474724] [ 1474.82278227  1474.82340967] [ -1.88081216e-12  -1.43155505e-12]
[ 729.6469802  -729.64708356] [ 

[ 1588.94697957  1588.94714578] [ 1489.63763753  1489.63810499] [  9.35215879e-14  -2.24865834e-13]
[ 736.97638553 -736.97646253] [ 690.91528924 -690.91550582] [ -9.35282470e-14   2.24866860e-13]
[ 1562.25727637 -1562.25712545] [ 1464.61633808 -1464.61591362] [ -4.51298688e-10  -1.37255046e-10]
[ 1540.15657545 -1540.15673483] [ 1443.89664006 -1443.89708833] [  6.46566905e-15  -4.59425196e-14]
[ 1194.48825244 -1194.48853141] [ 1119.83247513 -1119.83325973] [  5.51493944e-08  -8.69171430e-08]
[ 1354.99836022 -1354.99837277] [ 1270.31095094 -1270.31098624] [ -6.44950016e-15   4.59471714e-14]
[ 1114.98483055 -1114.98481307] [ 1045.29829502 -1045.29824586] [  4.82046573e-10   1.44171495e-10]
[ 705.21063694 -705.21063516] [ 661.13497379 -661.1349688 ] [  5.16518302e-13  -1.15855493e-12]
[-773.26022487  773.25999353] [-724.93167769  724.93102705] [ -8.24823383e-18  -9.83284852e-18]
[-1556.04617566  1556.04611723] [-1458.79334446  1458.79318013] [ -5.51806588e-08   8.69113851e-08]
[ 1590.53592